In [3]:
import numpy as np 
#import pandas as pd 
import matplotlib.pyplot as plt 
import seaborn as sns 
%matplotlib inline

import warnings

warnings.filterwarnings('ignore')
import pandas as pd
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split

In [5]:
df = pd.read_csv("C:/Users/HOME/Desktop/dataset/kaggle_dataset/pulsar star/pulsar_data_train.csv")


In [6]:
# remove leading spaces from column names

df.columns = train_df.columns.str.strip()


In [7]:
df.columns = ['IP Mean', 'IP Sd', 'IP Kurtosis', 'IP Skewness', 
              'DM-SNR Mean', 'DM-SNR Sd', 'DM-SNR Kurtosis', 'DM-SNR Skewness', 'target_class']

In [8]:
df['target_class'].value_counts()

0.0    11375
1.0     1153
Name: target_class, dtype: int64

In [9]:
df['target_class'].value_counts()/np.float(len(train_df))

0.0    0.907966
1.0    0.092034
Name: target_class, dtype: float64

In [11]:
# view summary of dataset

df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 12528 entries, 0 to 12527
Data columns (total 9 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   IP Mean          12528 non-null  float64
 1   IP Sd            12528 non-null  float64
 2   IP Kurtosis      10793 non-null  float64
 3   IP Skewness      12528 non-null  float64
 4   DM-SNR Mean      12528 non-null  float64
 5   DM-SNR Sd        11350 non-null  float64
 6   DM-SNR Kurtosis  12528 non-null  float64
 7   DM-SNR Skewness  11903 non-null  float64
 8   target_class     12528 non-null  float64
dtypes: float64(9)
memory usage: 881.0 KB


In [12]:
import pandas_profiling as pp

In [13]:
df.profile_report()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [14]:
df.isna().sum()

IP Mean               0
IP Sd                 0
IP Kurtosis        1735
IP Skewness           0
DM-SNR Mean           0
DM-SNR Sd          1178
DM-SNR Kurtosis       0
DM-SNR Skewness     625
target_class          0
dtype: int64

In [15]:
df['IP Kurtosis'].fillna((df['IP Kurtosis'].median()), inplace=True)
df['DM-SNR Sd'].fillna((df['DM-SNR Sd'].median()), inplace=True)
df['DM-SNR Skewness'].fillna((df['DM-SNR Skewness'].median()), inplace=True)


In [16]:
df.isna().sum()

IP Mean            0
IP Sd              0
IP Kurtosis        0
IP Skewness        0
DM-SNR Mean        0
DM-SNR Sd          0
DM-SNR Kurtosis    0
DM-SNR Skewness    0
target_class       0
dtype: int64

In [19]:
y=df['target_class']
x=df.drop('target_class',axis=1)

In [20]:
X_train,X_test,y_train,y_test=train_test_split(x,y,test_size=0.1,random_state=42)

In [21]:

scaler = StandardScaler()

X_train = scaler.fit_transform(X_train)

X_test = scaler.transform(X_test)


In [25]:
from sklearn.metrics import classification_report,confusion_matrix
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score

# Manual Search

We will use a Random Forest Classifier as our model to optimize.Random Forest models are formed by a large number of uncorrelated decision trees, which joint together constitute an ensemble. In Random Forest, each decision tree makes its own prediction and the overall model output is selected to be the prediction which appeared most frequently.

We can now start by calculating our base model accuracy.

In [26]:
model = RandomForestClassifier(random_state= 101).fit(X_train,y_train)
predictionforest = model.predict(X_test)
print(confusion_matrix(y_test,predictionforest))
print(classification_report(y_test,predictionforest))
acc1 = accuracy_score(y_test,predictionforest)

[[1130    8]
 [  24   91]]
              precision    recall  f1-score   support

         0.0       0.98      0.99      0.99      1138
         1.0       0.92      0.79      0.85       115

    accuracy                           0.97      1253
   macro avg       0.95      0.89      0.92      1253
weighted avg       0.97      0.97      0.97      1253



When using Manual Search, we choose some model hyperparameters based on our judgment/experience. We then train the model, evaluate its accuracy and start the process again. This loop is repeated until a satisfactory accuracy is scored.

The main parameters used by a Random Forest Classifier are:

* criterion = the function used to evaluate the quality of a split.

* max_depth = maximum number of levels allowed in each tree.

* max_features = maximum number of features considered when splitting a node.

* min_samples_leaf = minimum number of samples which can be stored in a tree leaf.

* min_samples_split = minimum number of samples necessary in a node to cause node splitting.

* n_estimators = number of trees in the ensemble.

In [28]:
model = RandomForestClassifier(n_estimators=10, random_state= 101).fit(X_train,y_train)
predictionforest = model.predict(X_test)
print(confusion_matrix(y_test,predictionforest))
print(classification_report(y_test,predictionforest))
acc2 = accuracy_score(y_test,predictionforest)

[[1135    3]
 [  23   92]]
              precision    recall  f1-score   support

         0.0       0.98      1.00      0.99      1138
         1.0       0.97      0.80      0.88       115

    accuracy                           0.98      1253
   macro avg       0.97      0.90      0.93      1253
weighted avg       0.98      0.98      0.98      1253



# Random Search

In Random Search, we create a grid of hyperparameters and train/test our model on just some random combination of these hyperparameters. In this example, I additionally decided to perform Cross-Validation on the training set.

When performing Machine Learning tasks, we generally divide our dataset in training and test sets. This is done so that to test our model after having trained it (in this way we can check it’s performances when working with unseen data). When using Cross-Validation, we divide our training set into N other partitions to make sure our model is not overfitting our data.

One of the most common used Cross-Validation methods is K-Fold Validation. In K-Fold, we divide our training set into N partitions and then iteratively train our model using N-1 partitions and test it with the left-over partition (at each iteration we change the left-over partition). Once having trained N times the model we then average the training results obtained in each iteration to obtain our overall training performance results.

Using Cross-Validation when implementing Hyperparameters optimization can be really important. In this way, we might avoid using some Hyperparameters which works really good on the training data but not so good with the test data. We can now start implementing Random Search by first defying a grid of hyperparameters which will be randomly sampled when calling RandomizedSearchCV().

In [29]:
import numpy as np 
from sklearn.model_selection import RandomizedSearchCV
from sklearn.model_selection import cross_val_score

random_search = {'criterion': ['entropy', 'gini'],
               'max_depth': [2],
               'max_features': ['auto', 'sqrt'],
               'min_samples_leaf': [4, 6, 8],
               'min_samples_split': [5, 7,10],
               'n_estimators': [20]}

clf = RandomForestClassifier()
model = RandomizedSearchCV(estimator = clf, param_distributions = random_search, n_iter = 10, 
                               cv = 4, verbose= 1, random_state= 101, n_jobs = -1)
model.fit(X_train,y_train)

Fitting 4 folds for each of 10 candidates, totalling 40 fits


RandomizedSearchCV(cv=4, estimator=RandomForestClassifier(), n_jobs=-1,
                   param_distributions={'criterion': ['entropy', 'gini'],
                                        'max_depth': [2],
                                        'max_features': ['auto', 'sqrt'],
                                        'min_samples_leaf': [4, 6, 8],
                                        'min_samples_split': [5, 7, 10],
                                        'n_estimators': [20]},
                   random_state=101, verbose=1)

In [30]:
import seaborn as sns

table = pd.pivot_table(pd.DataFrame(model.cv_results_),
    values='mean_test_score', index='param_n_estimators', 
                       columns='param_criterion')
     
sns.heatmap(table)

<AxesSubplot:xlabel='param_criterion', ylabel='param_n_estimators'>

# We can now evaluate how our model performed using Random Search. In this case, using Random Search leads to a consistent increase in accuracy compared to our base model.

In [31]:
predictionforest = model.best_estimator_.predict(X_test)
print(confusion_matrix(y_test,predictionforest))
print(classification_report(y_test,predictionforest))
acc3 = accuracy_score(y_test,predictionforest)

[[1136    2]
 [  31   84]]
              precision    recall  f1-score   support

         0.0       0.97      1.00      0.99      1138
         1.0       0.98      0.73      0.84       115

    accuracy                           0.97      1253
   macro avg       0.98      0.86      0.91      1253
weighted avg       0.97      0.97      0.97      1253



# Grid Search

 Grid Search, we set up a grid of hyperparameters and train/test our model on each of the possible combinations. In order to choose the parameters to use in Grid Search, we can now look at which parameters worked best with Random Search and form a grid based on them to see if we can find a better combination.

Grid Search can be implemented in Python using scikit-learn GridSearchCV() function.

In [32]:
from sklearn.model_selection import GridSearchCV

grid_search = {'criterion': ['entropy', 'gini'],
               'max_depth': [2],
               'max_features': ['auto', 'sqrt'],
               'min_samples_leaf': [4, 6, 8],
               'min_samples_split': [5, 7,10],
               'n_estimators': [20]}

clf = RandomForestClassifier()
model = GridSearchCV(estimator = clf, param_grid = grid_search, 
                               cv = 4, verbose= 5, n_jobs = -1)
model.fit(X_train,y_train)

predictionforest = model.best_estimator_.predict(X_test)
print(confusion_matrix(y_test,predictionforest))
print(classification_report(y_test,predictionforest))
acc4 = accuracy_score(y_test,predictionforest)

Fitting 4 folds for each of 36 candidates, totalling 144 fits
[[1135    3]
 [  31   84]]
              precision    recall  f1-score   support

         0.0       0.97      1.00      0.99      1138
         1.0       0.97      0.73      0.83       115

    accuracy                           0.97      1253
   macro avg       0.97      0.86      0.91      1253
weighted avg       0.97      0.97      0.97      1253



Grid Search is slower compared to Random Search but it can be overall more effective because it can go through the whole search space. Instead, Random Search can be faster fast but might miss some important points in the search space.

# Automated Hyperparameter Tuning


As we have seen above tuning machine learning hyperparameters is indeed a tedious but crucial task, as the performance of an algorithm can be highly dependent on the choice of hyperparameters. Manual tuning takes time away from important steps of the machine learning pipeline like feature engineering and interpreting results. Grid and random search are hands-off, but require long run times because they waste time evaluating unpromising areas of the search space. Increasingly, hyperparameter tuning is done by automated methods that aim to find optimal hyperparameters in less time using an informed search with no manual effort necessary beyond the initial set-up.

When using Automated Hyperparameter Tuning, the model hyperparameters to use are identified using techniques such as: Bayesian Optimization, Gradient Descent and Evolutionary Algorithms.

# Bayesian Optimization using HyperOpt

Bayesian optimization, a model-based method for finding the minimum of a function,while the final aim is to find the input value to a function which can give us the lowest possible output value has resulted in achieving better performance while requiring fewer iterations than random search. Bayesian Optimization can, therefore, lead to better performance in the testing phase and reduced optimization time.

Bayesian Optimization can be performed in Python using the Hyperopt library.

Hyperopt, Bayesian Optimization can be implemented giving 3 three main parameters to the function fmin().

** Objective Function = defines the loss function to minimize.

** Domain Space = defines the range of input values to test (in Bayesian Optimization this space creates a probability distribution for each of the used Hyperparameters).

** Optimization Algorithm = defines the search algorithm to use to select the best input values to use in each new iteration.

** Additionally, can also be defined in fmin() the maximum number of evaluations to perform.

Bayesian Optimization can reduce the number of search iterations by choosing the input values bearing in mind the past outcomes. In this way, we can concentrate our search from the beginning on values which are closer to our desired output. We can now run our Bayesian Optimizer using the fmin() function. A Trials() object is first created to make possible to visualize later what was going on while the fmin() function was running (eg. how the loss function was changing and how to used Hyperparameters were changing).

Hyperopt is one of several automated hyperparameter tuning libraries using Bayesian optimization. These libraries differ in the algorithm used to both construct the surrogate (probability model) of the objective function and choose the next hyperparameters to evaluate in the objective function. Hyperopt uses the Tree Parzen Estimator (TPE). Other Python libraries include Spearmint, which uses a Gaussian process for the surrogate, and SMAC, which uses a random forest regression.

Hyperopt has a simple syntax for structuring an optimization problem which extends beyond hyperparameter tuning to any problem that involves minimizing a function.

In [35]:
from hyperopt import hp, fmin, tpe, STATUS_OK, Trials

space = {'criterion': hp.choice('criterion', ['entropy', 'gini']),
        'max_depth': hp.quniform('max_depth', 10, 12, 10),
        'max_features': hp.choice('max_features', ['auto', 'sqrt','log2', None]),
        'min_samples_leaf': hp.uniform ('min_samples_leaf', 0, 0.5),
        'min_samples_split' : hp.uniform ('min_samples_split', 0, 1),
        'n_estimators' : hp.choice('n_estimators', [10, 50])
    }

def objective(space):
    model = RandomForestClassifier(criterion = space['criterion'], 
                                   max_depth = space['max_depth'],
                                 max_features = space['max_features'],
                                 min_samples_leaf = space['min_samples_leaf'],
                                 min_samples_split = space['min_samples_split'],
                                 n_estimators = space['n_estimators'], 
                                 )
    
    accuracy = cross_val_score(model, X_train, y_train, cv = 4).mean()

    # We aim to maximize accuracy, therefore we return it as a negative value
    return {'loss': -accuracy, 'status': STATUS_OK }
    
trials = Trials()
best = fmin(fn= objective,
            space= space,
            algo= tpe.suggest,
            max_evals = 20,
            trials= trials)
best

100%|██████████████████████████████████████████████████| 20/20 [00:07<00:00,  2.61it/s, best loss: -0.9697557900095444]


{'criterion': 1,
 'max_depth': 10.0,
 'max_features': 3,
 'min_samples_leaf': 0.03770837662189891,
 'min_samples_split': 0.5017751453643413,
 'n_estimators': 0}

We can now retrieve the set of best parameters identified and test our model using the best dictionary created during training. Some of the parameters have been stored in the best dictionary numerically using indices, therefore, we need first to convert them back as strings before input them in our Random Forest.

In [36]:
crit = {0: 'entropy', 1: 'gini'}
feat = {0: 'auto', 1: 'sqrt', 2: 'log2', 3: None}
est = {0: 10, 1: 50, 2: 75, 3: 100, 4: 125}

trainedforest = RandomForestClassifier(criterion = crit[best['criterion']], 
                                       max_depth = best['max_depth'], 
                                       max_features = feat[best['max_features']], 
                                       min_samples_leaf = best['min_samples_leaf'], 
                                       min_samples_split = best['min_samples_split'], 
                                       n_estimators = est[best['n_estimators']]
                                      ).fit(X_train,y_train)
predictionforest = trainedforest.predict(X_test)
print(confusion_matrix(y_test,predictionforest))
print(classification_report(y_test,predictionforest))
acc5 = accuracy_score(y_test,predictionforest)

[[1137    1]
 [  31   84]]
              precision    recall  f1-score   support

         0.0       0.97      1.00      0.99      1138
         1.0       0.99      0.73      0.84       115

    accuracy                           0.97      1253
   macro avg       0.98      0.86      0.91      1253
weighted avg       0.97      0.97      0.97      1253



# Genetic Algorithms using TPOT

In computer science and operations research, a genetic algorithm (GA) is a metaheuristic inspired by the process of natural selection that belongs to the larger class of evolutionary algorithms (EA). Genetic algorithms are commonly used to generate high-quality solutions to optimization and search problems by relying on biologically inspired operators such as mutation, crossover and selection.

Genetic Algorithms tries to apply natural selection mechanisms to Machine Learning contexts. They are inspired by the Darwinian process of Natural Selection and they are therefore also usually called as Evolutionary Algorithms.Let’s imagine we create a population of N Machine Learning models with some predefined Hyperparameters. We can then calculate the accuracy of each model and decide to keep just half of the models (the ones that perform best). We can now generate some offsprings having similar Hyperparameters to the ones of the best models so that to get again a population of N models. At this point, we can again calculate the accuracy of each model and repeat the cycle for a defined number of generations. In this way, just the best models will survive at the end of the process.

In order to implement Genetic Algorithms in Python, we can use the TPOT Auto Machine Learning library. TPOT is built on the scikit-learn library and it can

In [39]:
from tpot import TPOTClassifier
parameters = {'criterion': ['entropy', 'gini'],
               'max_depth': [2],
               'max_features': ['auto'],
               'min_samples_leaf': [4, 12],
               'min_samples_split': [5, 10],
               'n_estimators': [10]}
               
tpot_classifier = TPOTClassifier(generations= 4, population_size= 24, offspring_size= 12,
                                 verbosity= 2, early_stop= 12,
                                 config_dict=
                                 {'sklearn.ensemble.RandomForestClassifier': parameters}, 
                                 cv = 4, scoring = 'accuracy')
tpot_classifier.fit(X_train,y_train) 

Optimization Progress:   0%|          | 0/72 [00:00<?, ?pipeline/s]


Generation 1 - Current best internal CV score: 0.9770286905417991

Generation 2 - Current best internal CV score: 0.9770287220123208

Generation 3 - Current best internal CV score: 0.9770287220123208

Generation 4 - Current best internal CV score: 0.9770287220123208

Best pipeline: RandomForestClassifier(RandomForestClassifier(input_matrix, criterion=gini, max_depth=2, max_features=auto, min_samples_leaf=12, min_samples_split=10, n_estimators=10), criterion=gini, max_depth=2, max_features=auto, min_samples_leaf=4, min_samples_split=10, n_estimators=10)


TPOTClassifier(config_dict={'sklearn.ensemble.RandomForestClassifier': {'criterion': ['entropy',
                                                                                      'gini'],
                                                                        'max_depth': [2],
                                                                        'max_features': ['auto'],
                                                                        'min_samples_leaf': [4,
                                                                                             12],
                                                                        'min_samples_split': [5,
                                                                                              10],
                                                                        'n_estimators': [10]}},
               cv=4, early_stop=12, generations=4, offspring_size=12,
               population_size=24, scoring='accuracy', verbosity

The training report and the best parameters are identified above using Genetic Algorithms.

The overall accuracy of our Random Forest Genetic Algorithm optimized model is shown below.

In [40]:
accuracy = tpot_classifier.score(X_test, y_test)
print(accuracy)

0.9744612928970471


# Artificial Neural Networks (ANNs) Tuning

Using KerasClassifier wrapper, it is possible to apply Grid Search and Random Search for Deep Learning models in the same way it was done when using scikit-learn Machine Learning models. In the following example, we will try to optimize some of our ANN parameters such as: how many neurons to use in each layer and which activation function and optimizer to use.

In [41]:
from keras.models import Sequential
from keras.layers import Dense, Dropout
from keras.wrappers.scikit_learn import KerasClassifier

In [42]:
def DL_Model(activation= 'linear', neurons= 5, optimizer='Adam'):
    model = Sequential()
    model.add(Dense(neurons, input_dim= 4, activation= activation))
    model.add(Dense(neurons, activation= activation))
    model.add(Dropout(0.3))
    model.add(Dense(1, activation='sigmoid'))
    model.compile(loss='binary_crossentropy', optimizer= optimizer, metrics=['accuracy'])
    return model

In [43]:
# Defining grid parameters
activation = ['softmax', 'relu']
neurons = [5, 10]
optimizer = ['Adam', 'Adamax']
param_grid = dict(activation = activation, neurons = neurons, optimizer = optimizer)

clf = KerasClassifier(build_fn= DL_Model, epochs= 5, batch_size=1024, verbose= 2)

In [44]:
model = GridSearchCV(estimator= clf, param_grid=param_grid, n_jobs=-1)
model.fit(X_train,y_train)

Epoch 1/5


ValueError: in user code:

    E:\ANAXONDA\lib\site-packages\keras\engine\training.py:853 train_function  *
        return step_function(self, iterator)
    E:\ANAXONDA\lib\site-packages\keras\engine\training.py:842 step_function  **
        outputs = model.distribute_strategy.run(run_step, args=(data,))
    E:\ANAXONDA\lib\site-packages\tensorflow\python\distribute\distribute_lib.py:1286 run
        return self._extended.call_for_each_replica(fn, args=args, kwargs=kwargs)
    E:\ANAXONDA\lib\site-packages\tensorflow\python\distribute\distribute_lib.py:2849 call_for_each_replica
        return self._call_for_each_replica(fn, args, kwargs)
    E:\ANAXONDA\lib\site-packages\tensorflow\python\distribute\distribute_lib.py:3632 _call_for_each_replica
        return fn(*args, **kwargs)
    E:\ANAXONDA\lib\site-packages\keras\engine\training.py:835 run_step  **
        outputs = model.train_step(data)
    E:\ANAXONDA\lib\site-packages\keras\engine\training.py:787 train_step
        y_pred = s

#                         Optuna

Optuna is an automatic hyperparameter optimization software framework, particularly designed for machine learning. It features an imperative, define-by-run style user API. Optuna is a framework designed for the automation and the acceleration of the optimization studies.

Key Features:

* Eager search spaces: Automated search for optimal hyperparameters using Python conditionals, loops, and syntax

* State-of-the-art algorithms: Efficiently search large spaces and prune unpromising trials for faster results

* Easy parallelization: Parallelize hyperparameter searches over multiple threads or processes without modifying code

We use the terms study and trial as follows:

* Study: optimization based on an objective function

* Trial: a single execution of the objective function

The goal of a study is to find out the optimal set of hyperparameter values (e.g., classifier and svm_c) through multiple trials (e.g., n_trials=100).

We can optimize Scikit-Learn hyperparameters, such as the C parameter of SVC and the max_depth of the RandomForestClassifier, in three steps:

* Wrap model training with an objective function and return accuracy

* Suggest hyperparameters using a trial object

* Create a study object and execute the optimization

In [46]:
import sklearn
import sklearn.datasets
import sklearn.ensemble
import sklearn.model_selection
import sklearn.svm
import optuna

In [47]:
# 1. Define an objective function to be maximized.
def objective(trial):
    iris = sklearn.datasets.load_iris()
    x, y = iris.data, iris.target
    # 2. Suggest values for the hyperparameters using a trial object.
    classifier_name = trial.suggest_categorical('classifier', ['SVC', 'RandomForest'])
    if classifier_name == 'SVC':
         svc_c = trial.suggest_loguniform('svc_c', 1e-10, 1e10)
         classifier_obj = sklearn.svm.SVC(C=svc_c, gamma='auto')
    else:
        rf_max_depth = int(trial.suggest_loguniform('rf_max_depth', 2, 32))
        classifier_obj = sklearn.ensemble.RandomForestClassifier(max_depth=rf_max_depth, n_estimators=10)
    ...
    return accuracy


# 3. Create a study object and optimize the objective function.
study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=100)

[I 2021-10-10 16:59:43,354] Finished trial#0 resulted in value: 0.9744612928970471. Current best value is 0.9744612928970471 with parameters: {'classifier': 'SVC', 'svc_c': 4.2712638380810375e-09}.
[I 2021-10-10 16:59:43,513] Finished trial#1 resulted in value: 0.9744612928970471. Current best value is 0.9744612928970471 with parameters: {'classifier': 'SVC', 'svc_c': 4.2712638380810375e-09}.
[I 2021-10-10 16:59:43,673] Finished trial#2 resulted in value: 0.9744612928970471. Current best value is 0.9744612928970471 with parameters: {'classifier': 'SVC', 'svc_c': 4.2712638380810375e-09}.
[I 2021-10-10 16:59:43,835] Finished trial#3 resulted in value: 0.9744612928970471. Current best value is 0.9744612928970471 with parameters: {'classifier': 'SVC', 'svc_c': 4.2712638380810375e-09}.
[I 2021-10-10 16:59:43,999] Finished trial#4 resulted in value: 0.9744612928970471. Current best value is 0.9744612928970471 with parameters: {'classifier': 'SVC', 'svc_c': 4.2712638380810375e-09}.
[I 2021-10

[I 2021-10-10 16:59:50,480] Finished trial#41 resulted in value: 0.9744612928970471. Current best value is 0.9744612928970471 with parameters: {'classifier': 'SVC', 'svc_c': 4.2712638380810375e-09}.
[I 2021-10-10 16:59:50,644] Finished trial#42 resulted in value: 0.9744612928970471. Current best value is 0.9744612928970471 with parameters: {'classifier': 'SVC', 'svc_c': 4.2712638380810375e-09}.
[I 2021-10-10 16:59:50,819] Finished trial#43 resulted in value: 0.9744612928970471. Current best value is 0.9744612928970471 with parameters: {'classifier': 'SVC', 'svc_c': 4.2712638380810375e-09}.
[I 2021-10-10 16:59:50,989] Finished trial#44 resulted in value: 0.9744612928970471. Current best value is 0.9744612928970471 with parameters: {'classifier': 'SVC', 'svc_c': 4.2712638380810375e-09}.
[I 2021-10-10 16:59:51,161] Finished trial#45 resulted in value: 0.9744612928970471. Current best value is 0.9744612928970471 with parameters: {'classifier': 'SVC', 'svc_c': 4.2712638380810375e-09}.
[I 20

[I 2021-10-10 16:59:57,644] Finished trial#82 resulted in value: 0.9744612928970471. Current best value is 0.9744612928970471 with parameters: {'classifier': 'SVC', 'svc_c': 4.2712638380810375e-09}.
[I 2021-10-10 16:59:57,851] Finished trial#83 resulted in value: 0.9744612928970471. Current best value is 0.9744612928970471 with parameters: {'classifier': 'SVC', 'svc_c': 4.2712638380810375e-09}.
[I 2021-10-10 16:59:58,056] Finished trial#84 resulted in value: 0.9744612928970471. Current best value is 0.9744612928970471 with parameters: {'classifier': 'SVC', 'svc_c': 4.2712638380810375e-09}.
[I 2021-10-10 16:59:58,261] Finished trial#85 resulted in value: 0.9744612928970471. Current best value is 0.9744612928970471 with parameters: {'classifier': 'SVC', 'svc_c': 4.2712638380810375e-09}.
[I 2021-10-10 16:59:58,469] Finished trial#86 resulted in value: 0.9744612928970471. Current best value is 0.9744612928970471 with parameters: {'classifier': 'SVC', 'svc_c': 4.2712638380810375e-09}.
[I 20

# TUNE

Tune is a Python library for experiment execution and hyperparameter tuning at any scale. Core features:

* Launch a multi-node distributed hyperparameter sweep in less than 10 lines of code.

* Supports any machine learning framework, including PyTorch, XGBoost, MXNet, and Keras.

* Natively integrates with optimization libraries such as HyperOpt, Bayesian Optimization, and Facebook Ax.

* Choose among scalable algorithms such as Population Based Training (PBT), Vizier’s Median Stopping Rule, HyperBand/ASHA.

* Visualize results with TensorBoard.

* Move your models from training to serving on the same infrastructure with Ray Serve.

In [49]:
import torch.optim as optim
from ray import tune
from ray.tune.examples.mnist_pytorch import get_data_loaders, train, test


In [50]:
def train_mnist(config):
    train_loader, test_loader = get_data_loaders()
    model = ConvNet()
    optimizer = optim.SGD(model.parameters(), lr=config["lr"])
    for i in range(10):
        train(model, optimizer, train_loader)
        acc = test(model, test_loader)
        tune.report(mean_accuracy=acc)

In [51]:
analysis = tune.run(train_mnist, config={"lr": tune.grid_search([0.001, 0.01, 0.1])})
print("Best config: ", analysis.get_best_config(metric="mean_accuracy"))

2021-10-10 17:06:28,530	WARNING function_runner.py:558 -- Function checkpointing is disabled. This may result in unexpected behavior when using checkpointing features or certain schedulers. To enable, set the train function arguments to be `func(config, checkpoint_dir=None)`.


2021-10-10 17:06:28,916	ERROR syncer.py:72 -- Log sync requires rsync to be installed.


(pid=4948) Downloading http://yann.lecun.com/exdb/mnist/train-images-idx3-ubyte.gz
(pid=4948) Downloading http://yann.lecun.com/exdb/mnist/train-images-idx3-ubyte.gz to C:\Users\HOME/data\MNIST\raw\train-images-idx3-ubyte.gz


 90%|████████▉ | 8918016/9912422 [00:02<00:00, 4237342.93it/s]
9913344it [00:02, 3651474.58it/s]                             


(pid=4948) Extracting C:\Users\HOME/data\MNIST\raw\train-images-idx3-ubyte.gz to C:\Users\HOME/data\MNIST\raw
(pid=4948) 
(pid=4948) Downloading http://yann.lecun.com/exdb/mnist/train-labels-idx1-ubyte.gz
(pid=4948) Downloading http://yann.lecun.com/exdb/mnist/train-labels-idx1-ubyte.gz to C:\Users\HOME/data\MNIST\raw\train-labels-idx1-ubyte.gz
(pid=4948) Extracting C:\Users\HOME/data\MNIST\raw\train-labels-idx1-ubyte.gz to C:\Users\HOME/data\MNIST\raw
(pid=4948) 
(pid=4948) Downloading http://yann.lecun.com/exdb/mnist/t10k-images-idx3-ubyte.gz


...

Result for train_mnist_4ee3a_00001:


  {}
  

(pid=4428)     self.run()
(pid=4428)   File "E:\ANAXONDA\lib\site-packages\ray\tune\function_runner.py", line 279, in run
(pid=4428)     raise e
(pid=4428)   File "E:\ANAXONDA\lib\site-packages\ray\tune\function_runner.py", line 260, in run
(pid=4428)     self._entrypoint()


(pid=4428)   File "E:\ANAXONDA\lib\site-packages\ray\tune\function_runner.py", line 328, in entrypoint
(pid=4428)     return self._trainable_func(self.config, self._status_reporter,
(pid=4428)   File "E:\ANAXONDA\lib\site-packages\ray\tune\function_runner.py", line 594, in _trainable_func
(pid=4428)     output = fn()
(pid=4428)   File "C:\Users\HOME\AppData\Local\Temp/ipykernel_704/627987275.py", line 3, in train_mnist
(pid=4428) NameError: name 'ConvNet' is not defined
(pid=2100) E:\ANAXONDA\lib\site-packages\torchvision\datasets\mnist.py:498: UserWarning: The given NumPy array is not writeable, and PyTorch does not support non-writeable tensors. This means you can write to the underlying (supposedly non-writeable) NumPy array using the tensor. You may want to copy the array to protect its data or make it writeable before converting it to a tensor. This type of warning will be suppressed for the rest of this program. (Triggered internally at  ..\torch\csrc\utils\tensor_numpy.cpp:180.)

TuneError: ('Trials did not complete', [train_mnist_4ee3a_00000, train_mnist_4ee3a_00001, train_mnist_4ee3a_00002])

# SHERPA

Sherpa can automatically run parallel evaluations on a cluster using a job scheduler such as SGE. Simply provide a Python script that takes a set of hyperparameters as arguments and performs a single trial evaluation. A database collects the partial results in real-time, and the hyperparameter optimization algorithm decides what to do next.

SHERPA is a Python library for hyperparameter tuning of machine learning models. It provides:

* Hyperparameter optimization for machine learning researchers

* It can be used with any Python machine learning library such as Keras, Tensorflow, PyTorch, or Scikit-Learn

* A choice of hyperparameter optimization algorithms such as Bayesian optimization via GPyOpt, Asynchronous Successive Halving (aka Hyperband) , and Population Based Training .

* Parallel computation that can be fitted to the user's needs

* A live dashboard for the exploratory analysis of results.

In [52]:
!pip install parameter-sherpa

  Created wheel for parameter-sherpa: filename=parameter_sherpa-1.0.6-py2.py3-none-any.whl size=542120 sha256=a8a77c5252216b9a507d86e5eac7bdbe0c4a2d09d65ee398f52c8151085aea63
  Stored in directory: c:\users\home\appdata\local\pip\cache\wheels\e3\d3\76\3d862b552967f9f1220800bc3b27dba7aa5a6ae5596a79b006
  Created wheel for GPyOpt: filename=GPyOpt-1.2.6-py3-none-any.whl size=83621 sha256=776e89d00038d69ebc75338f32953377247f29eec8ffdf1a5fb5f118ba0bcc9b
  Stored in directory: c:\users\home\appdata\local\pip\cache\wheels\5e\0b\6f\65b7572b74ce7c031e4c68556b8fd43c210f5b9415937c429d
  Created wheel for paramz: filename=paramz-0.9.5-py3-none-any.whl size=102551 sha256=d3caa5e858c54a44c3823e60209c60e7b612d2256abf03c1ac87ab9333b98934
  Stored in directory: c:\users\home\appdata\local\pip\cache\wheels\66\78\6c\d98cb437834de5e29381786b4ba8a77ea68cca74653ab62713
Successfully built parameter-sherpa GPyOpt paramz


In [57]:
from sklearn.datasets import load_breast_cancer
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import cross_val_score
import time
import sherpa
import sherpa.algorithms.bayesian_optimization as bayesian_optimization

parameters = [sherpa.Discrete('n_estimators', [2, 50]),
sherpa.Choice('criterion', ['gini', 'entropy']),
sherpa.Continuous('max_features', [0.1, 0.9])]

algorithm = bayesian_optimization.GPyOpt(max_concurrent=1,
model_type='GP_MCMC',
acquisition_type='EI_MCMC',
max_num_trials=10)

X, y = load_breast_cancer(return_X_y=True)
study = sherpa.Study(parameters=parameters,
algorithm=algorithm,
disable_dashboard=True,
lower_is_better=False)

for trial in study:
    print("Trial ", trial.id, " with parameters ", trial.parameters)
    clf = RandomForestClassifier(criterion=trial.parameters['criterion'],
    max_features=trial.parameters['max_features'],
    n_estimators=trial.parameters['n_estimators'],
    random_state=0)
    scores = cross_val_score(clf, X, y, cv=5)
    print("Score: ", scores.mean())
    study.add_observation(trial, iteration=1, objective=scores.mean())
    study.finalize(trial)
    print(study.get_best_result())

study.save(".")

Trial  1  with parameters  {'n_estimators': 8, 'criterion': 'entropy', 'max_features': 0.4140505385748001}
Score:  0.9542928116752056
{'Trial-ID': 1, 'Iteration': 1, 'criterion': 'entropy', 'max_features': 0.4140505385748001, 'n_estimators': 8, 'Objective': 0.9542928116752056}
Trial  2  with parameters  {'n_estimators': 12, 'criterion': 'entropy', 'max_features': 0.6360792365346456}
Score:  0.9508306163639186
{'Trial-ID': 1, 'Iteration': 1, 'criterion': 'entropy', 'max_features': 0.4140505385748001, 'n_estimators': 8, 'Objective': 0.9542928116752056}
Trial  3  with parameters  {'n_estimators': 38, 'criterion': 'gini', 'max_features': 0.7108740500986805}
Score:  0.9666666666666666
{'Trial-ID': 3, 'Iteration': 1, 'criterion': 'gini', 'max_features': 0.7108740500986805, 'n_estimators': 38, 'Objective': 0.9666666666666666}
Trial  4  with parameters  {'n_estimators': 21, 'criterion': 'gini', 'max_features': 0.6859377209384586}
Score:  0.9543393882937432
{'Trial-ID': 3, 'Iteration': 1, 'crit

INFO:GP:initializing Y
INFO:GP:initializing inference method
INFO:GP:adding kernel and likelihood as parameters


Trial  5  with parameters  {'n_estimators': 38, 'criterion': 'gini', 'max_features': 0.7108740502524845}
Score:  0.9666666666666666
{'Trial-ID': 3, 'Iteration': 1, 'criterion': 'gini', 'max_features': 0.7108740500986805, 'n_estimators': 38, 'Objective': 0.9666666666666666}


INFO:GP:initializing Y
INFO:GP:initializing inference method
INFO:GP:adding kernel and likelihood as parameters


Trial  6  with parameters  {'n_estimators': 38, 'criterion': 'gini', 'max_features': 0.1}
Score:  0.9595870206489675
{'Trial-ID': 3, 'Iteration': 1, 'criterion': 'gini', 'max_features': 0.7108740500986805, 'n_estimators': 38, 'Objective': 0.9666666666666666}


...

Trial  8  with parameters  {'n_estimators': 38, 'criterion': 'gini', 'max_features': 0.6585311005743025}
Score:  0.9631268436578171
{'Trial-ID': 3, 'Iteration': 1, 'criterion': 'gini', 'max_features': 0.7108740500986805, 'n_estimators': 38, 'Objective': 0.9666666666666666}


INFO:GP:initializing Y
INFO:GP:initializing inference method
INFO:GP:adding kernel and likelihood as parameters


Trial  9  with parameters  {'n_estimators': 38, 'criterion': 'gini', 'max_features': 0.7138425586369984}
Score:  0.9666666666666666
{'Trial-ID': 3, 'Iteration': 1, 'criterion': 'gini', 'max_features': 0.7108740500986805, 'n_estimators': 38, 'Objective': 0.9666666666666666}


INFO:GP:initializing Y
INFO:GP:initializing inference method
INFO:GP:adding kernel and likelihood as parameters


Trial  10  with parameters  {'n_estimators': 38, 'criterion': 'gini', 'max_features': 0.7108369889756881}
Score:  0.9666666666666666
{'Trial-ID': 3, 'Iteration': 1, 'criterion': 'gini', 'max_features': 0.7108740500986805, 'n_estimators': 38, 'Objective': 0.9666666666666666}


In [59]:
print(study.get_best_result())

{'Trial-ID': 3, 'Iteration': 1, 'criterion': 'gini', 'max_features': 0.7108740500986805, 'n_estimators': 38, 'Objective': 0.9666666666666666}
